In [1]:
import music21
import json
import pandas as pd
import os
import multiprocessing as mp
from  chord_extractor.extractors import Chordino
import pickle
import numpy as np
import math
import subprocess
from typing import List, Callable, Optional

In [2]:
class ChordProcessor(object):
    def __init__(self, ch_profile_file, key_map_file, bass_base=36, chord_base=48):
        # bass_base=36 : C2
        # chord_base=48 : C3
        self.chord_profile = pickle.load(open(ch_profile_file, 'rb'))
        self.key_map = pickle.load(open(key_map_file, 'rb'))
        self.bass_base = bass_base  # the anchor for bass note
        self.chord_base = chord_base  # the anchor for list of chord notes

    # parse chord_literal to (tone,type,slash)
    def _parse_chord_literal(self, ch):
        if len(ch) < 2:
            # tone inside [C,D,E,F,G,n_df = pd.concat([a,b], axis=1)A,B]
            tone, ch_type, slash = ch[0], '', ''
        elif ch[1] in ['#', 'b']:
            # tone contains #,b
            tone, ch_type = ch[:2], ch[2:].split('/')
        else:
            tone, ch_type = ch[:1], ch[1:].split('/')

        if not ch_type:
            # triad with no slash
            ch_type, slash = '', ''
        elif len(ch_type) > 1:
            ch_type, slash = ch_type[0], ch_type[1]
        else:
            ch_type, slash = ch_type[0], ''

        # print ('[[parsed]] {} --> {} | {} | {}'.format(ch, tone, ch_type, slash))
        return tone, ch_type, slash

    # convert chord literal to list of notes
    def compute_notes(self, chord_literal, require_parsing=True, tone=None, ch_type=None, slash=None):
        if require_parsing:
            tone, ch_type, slash = self._parse_chord_literal(chord_literal)

        if not slash:
            slash = tone

        chord = list(np.asarray(self.chord_profile[ch_type]) + self.chord_base + self.key_map[tone])
        bass = self.bass_base + self.key_map[slash]

        # print ('(result) chord: {}, bass: {}'.format(chord, bass))
        # print ('-------------------------------------------------')
        return chord, bass

In [3]:
def create_chord_from_name(ch_p, ch):

    notes = []

    chord_type = ch.chord
    if chord_type != 'N':
        notes, bass = ch_p.compute_notes(ch.chord)
        notes = [int(n) for n in notes]
        
    chord = music21.chord.Chord(notes)

    return chord

In [4]:
def process_chord_change(chord_change, bps, interval=False):
#     chord = create_chord_from_name(chord_processor, chord_change)
    
#     if interval:
#         chord.transpose(interval, inPlace=True)
        
#     chord.simplifyEnharmonics(inPlace=True)

    start_sec = chord_change.timestamp
    start_beat = math.floor(start_sec * bps / 2.) * 2
    
    return chord_change.chord, start_beat, start_sec

In [5]:
def process_note(notes, i):
    note = notes[i]
    start_beat = note.offset
    end_beat =  float(start_beat) + float(note.duration.quarterLength)
    start_sec = notes[i-1] if i > 0 else 0
    end_sec = start_sec + note.seconds

    if type(note) == music21.chord.Chord:
        note = note.notes[-1]
        
    norm_beat = math.floor(start_beat / 2.) * 2
    beat_offest = start_beat - norm_beat
    
    return note.pitch.name + n.pitch.octave, norm_beat, beat_offest, start_sec

In [6]:
def preprocess(path: str):
    ext = os.path.splitext(path)[1]
    if ext in ['.mid', '.midi']:
        base = os.path.basename(path)
        file_name = os.path.splitext(base)[0]
        wav_file = os.path.join('/media/manu/Data/PycharmProjects/ai_music_project/data/extractor', file_name)

        if not os.path.isfile(wav_file):
#             print('Running timidity on {} to create {}'.format(path, wav_file))
            subprocess.run(['timidity', path, '--preserve-silence', '-Ow', '-o', wav_file])
#         else:
#             print('Returning already existing temporary wav file {}'.format(wav_file))
        return wav_file

    return None

In [7]:
def find_interval(score):
    try:
        key = score.analyze('key')
    except:
        print('NO KEY')
        return None

    print(key)

    if key.mode == 'minor':
        key = key.getRelativeMajor()
    
    tonic = music21.note.Note(key.tonic.name)
    interval = music21.interval.Interval(music21.note.Note('C'), c_note)
    
    return interval


In [12]:
#     for file in ['0040ae8f51d3c1c6174fe12b980c164e.mid']:

def extract_chords_and_melody(transpose, chord_processor, chordino, filename):   
    print(filename)
    
#     filename = f'../data/output/{file}'
#     song_id = file.split('.')[0]
    extension = filename[-3:]
    
    csv_filename = f'{filename[:-4]}.csv'
    
    if extension == 'mid':

#         if os.path.exists(csv_filename):
#             df = pd.read_csv(csv_filename)
            
#             if len(df['beat'].value_counts()) > 1:
#                 print(f'Skip {filename}')
#                 return
#             else:
#                 pass
#                 print('Re-doing it...')

#         name = names[song_id]
#         print(filename, name[0])

        try:
            score = music21.converter.parse(filename)
#             print('converted')
            conversion_file_path = preprocess(filename)
#             print('preprocessed')
            chords = chordino.extract(conversion_file_path)
#             print('extracted')
        except Exception as e:
#             print(f'ERROR! {e}')
            return

        score = score.parts[0]

        interval = False
#         if transpose:
#             print('Transpose')
#             interval = find_interval(score)
#             melody.transpose(interval, inPlace=True)
#         else:
#             pass
#             print('Don\'t transpose')

        if len(melody.flat.notesAndRests) == 0:
#             print('No notes')
            return
        else:
            pass
#             print(f'N. notes: {len(melody.flat.notesAndRests)}')

        prev_start_sec = 0
        prev_end_sec = 0
        bpm = 0

        n_df = pd.DataFrame(columns=['notes', 'norm_beat', 'beat_offset','timestamp'], 
    #                             data=[process_note(melody.flat.notesAndRests, interval) 
    #                             for i, note in enumerate(melody.notesAndRests) 
    #                             if not getattr(note, 'isRest', None) and not note.isRest]
                           )

        i = 0
        for note in melody.flat.notesAndRests:
            start_beat = note.offset
            end_beat =  float(start_beat) + float(note.duration.quarterLength)
            start_sec = prev_end_sec
            end_sec = start_sec + note.seconds

            if not getattr(note, 'isRest', None) or not note.isRest:
                if type(note) == music21.chord.Chord:
                    note = note.notes[-1]

                norm_beat = math.floor(start_beat / 2.) * 2
                beat_offest = start_beat - norm_beat
                note_name = note.pitch.name + str(note.pitch.octave)

                n_df.loc[i,:] = [note_name, norm_beat, beat_offest, round(start_sec, 3)]

                i+=1

            prev_end_sec = end_sec

        a = n_df.groupby('norm_beat')['notes'].apply(list)
        b = n_df.groupby('norm_beat')['beat_offset'].apply(list)
        c = n_df.groupby('norm_beat')['timestamp'].apply(list)
        n_df = pd.concat([a,b,c], axis=1).reset_index()

        bps = melody.metronomeMarkBoundaries()[0][-1].getQuarterBPM() / 60
#         print(f'BPS: {bps * 60}')

        c_df = pd.DataFrame(columns=['chord_name', 'beat', 'timestamp'], 
                            data=[process_chord_change(chord_change, bps, interval) 
                                  for chord_change in chords if chord_change.chord != 'N'] )
        
        r_df = pd.merge(n_df, c_df, 
                        left_on='norm_beat', right_on='beat', 
                        how='outer', suffixes=('_chord', '_notes')).sort_values('beat')
        r_df = pd.merge(n_df, c_df, 
                        left_on='norm_beat', right_on='beat', 
                        suffixes=('_chord', '_notes'), how='outer')
        r_df['beat'] = r_df['beat'].fillna(r_df['norm_beat'])
        r_df.drop('norm_beat', axis=1, inplace=True)
        r_df.to_csv(csv_filename, index=False)

#         print('-------------------------')


In [15]:
from functools import partial
import multiprocessing

transpose = False
chord_processor = ChordProcessor('../pickles/chord_profile.pkl', '../pickles/key_map.pkl')
chordino = Chordino(roll_on=5)


# folders = list(range(0, 10)) + ['a', 'b', 'c', 'd', 'e', 'f']
folders = list(range(0,4))


iterable = []
for folder in folders:
    directory = f'../data/output/{folder}'
    
    for dirpath,_,filenames in os.walk(directory):
        for f in filenames:
            iterable.append(os.path.join(dirpath, f))

# print(len(iterable))
# print(iterable[1])

# extract_chords_and_melody(transpose, chord_processor, chordino, iterable[2])

pool = multiprocessing.Pool(12)

func = partial(extract_chords_and_melody, transpose, chord_processor, chordino)

pool.map(func, iterable)
pool.close()
pool.join()

../data/output/0/09c9ca344cfeef35b7f8f9604383fdd6.mid../data/output/0/09147afaf4033305a1b8f8bb66d238f4.csv../data/output/0/0ca9c1c10d110f3ddca88ac1df9d74c1.csv../data/output/0/0f91954ec40b6bba958e55b2a21156de.csv../data/output/0/021272fb2af8da8c7117d5a40d156d76.csv../data/output/0/058455f78c24fa30e32ba23be93aad34.csv


../data/output/0/09f351efda3cc8e29f97d513bd4a3d59.csv
../data/output/0/06d351454f7988f2dc3c72745ad4e835.mid../data/output/0/03938f62ad702ffa1c03e876bfbaf608.csv../data/output/0/03685d6c32104a56263bf0fafa19a4a5.mid../data/output/0/05c341c2e83687c8602262529454ff9a.mid

../data/output/0/09147afaf4033305a1b8f8bb66d238f4.mid../data/output/0/04b08166c8364f160a47dc5a31e1167e.csv../data/output/0/0ca9c1c10d110f3ddca88ac1df9d74c1.mid
../data/output/0/0f91954ec40b6bba958e55b2a21156de.mid
../data/output/0/021272fb2af8da8c7117d5a40d156d76.mid


../data/output/0/058455f78c24fa30e32ba23be93aad34.mid


../data/output/0/09f351efda3cc8e29f97d513bd4a3d59.mid

../data/output/0/03938f62ad702

../data/output/0/0bf47f669192e8b74723602a660bad1b.mid
../data/output/0/06bcd0a7de8b370dc04fa6b438ed81f8.csv
../data/output/0/06bcd0a7de8b370dc04fa6b438ed81f8.mid
../data/output/0/003a540f83c8c68e6a383e7b111837b4.csv
../data/output/0/003a540f83c8c68e6a383e7b111837b4.mid
../data/output/0/098659a08731fffb8c4cb1d9a350717c.csv
../data/output/0/098659a08731fffb8c4cb1d9a350717c.mid
../data/output/0/0839750b061065c414a843bf4bb2e3c8.csv
../data/output/0/0839750b061065c414a843bf4bb2e3c8.mid
../data/output/0/040800122d9eac5c5607d0b9d9e12bd0.csv
../data/output/0/040800122d9eac5c5607d0b9d9e12bd0.mid
../data/output/0/0554b7a42fa225edbbded91f7bfe6985.csv
../data/output/0/0554b7a42fa225edbbded91f7bfe6985.mid
../data/output/0/003ab0f428fc5d4f9a31e29f707ea798.csv
../data/output/0/003ab0f428fc5d4f9a31e29f707ea798.mid
../data/output/0/0d9bd15c9c0e3c6d73e1df5943f51925.csv
../data/output/0/0da22dae245ee94580c5b47589895983.mid
../data/output/0/0839b08003080e76b6e165c63745992d.csv
../data/output/0/0839b080030

../data/output/0/0e25d6c30d56a5a519a18b01bae294ee.mid
../data/output/0/02e56eda8794514ac9a1f86e0c3482f0.csv
../data/output/0/02e56eda8794514ac9a1f86e0c3482f0.mid
../data/output/0/068a1c748530acfb65d175f335e467b0.csv
../data/output/0/068faf246ab781d976bc88ccce3af8e0.mid
../data/output/0/07de968d2384bedbf0b247afcf4cc53e.csv
../data/output/0/07de968d2384bedbf0b247afcf4cc53e.mid
../data/output/0/0a8c73ca79f5918407925bdc9f5f0088.csv
../data/output/0/0a8c73ca79f5918407925bdc9f5f0088.mid
../data/output/0/0ec264d4f0b5938d9d074e4b252e9d5e.csv
../data/output/0/0ec264d4f0b5938d9d074e4b252e9d5e.mid
../data/output/0/07ba5c5728c665ee9fa8edd1aff0d50e.csv
../data/output/0/07ba5c5728c665ee9fa8edd1aff0d50e.mid
../data/output/0/0a8d9154f04f66a70fb6c19a466c5adf.csv
../data/output/0/0a8d9154f04f66a70fb6c19a466c5adf.mid
../data/output/0/01a38c6f4c40f57b792c4f0808c23653.mid
../data/output/0/02a861b12beb510bc0a3d4a1725579f3.csv
../data/output/0/02a861b12beb510bc0a3d4a1725579f3.mid
../data/output/0/00d2f9e67bb

../data/output/0/02cfd441150769464a660bbe8995a7b3.csv
../data/output/0/02cfd441150769464a660bbe8995a7b3.mid
../data/output/0/002f27633d4cb0eda33bb7c612d5919b.mid
../data/output/0/0913a82cca3d799661f30e9c545554f2.csv
../data/output/0/0913a82cca3d799661f30e9c545554f2.mid
../data/output/0/0efd3e379c5c31027f20fa8c136eb7b4.csv
../data/output/0/0efd3e379c5c31027f20fa8c136eb7b4.mid
../data/output/0/00a08188cf4ae32b64e53a56b9072e06.csv
../data/output/0/00a793600d18f552c404c13d7d76066e.mid
../data/output/0/08863b5aa196c6849ddee42ba088162c.csv
../data/output/0/08863b5aa196c6849ddee42ba088162c.mid
../data/output/0/0689a2b89a4ab93c86d0a3598667a31a.csv
../data/output/0/0689a2b89a4ab93c86d0a3598667a31a.mid
../data/output/0/0369695de3b81cef6769c2b869d9675c.csv
../data/output/0/036f35e6dd1dbbdc59577067e86bac0f.mid
../data/output/0/0689f80b8a94bfaaf8f97660965c5405.csv
../data/output/0/0689f80b8a94bfaaf8f97660965c5405.mid
../data/output/0/0a42d440c6d20702dc61c783f572b3d4.csv
../data/output/0/0a42d440c6d

../data/output/0/0d0730808c79034322173dc94f7c1f2a.mid
../data/output/0/0cd679bef9b9e299430a0650bb523b85.csv
../data/output/0/0cd679bef9b9e299430a0650bb523b85.mid
../data/output/0/079105a25c573255b22af1bfa99c7427.csv
../data/output/0/079105a25c573255b22af1bfa99c7427.mid
../data/output/0/095825ec83b9174aacddaffc8498a086.csv
../data/output/0/095825ec83b9174aacddaffc8498a086.mid
../data/output/0/0d0786125a8c71c0e75a77ca54987fb0.csv
../data/output/0/0d0786125a8c71c0e75a77ca54987fb0.mid
../data/output/0/0337d41f39ed79019352034f560e2d2f.csv
../data/output/0/0337d41f39ed79019352034f560e2d2f.mid
../data/output/0/07269703eb7e5af88a37cb5bb0a29975.csv
../data/output/0/07269703eb7e5af88a37cb5bb0a29975.mid
../data/output/0/05ca2180d1a20feab0a4a26fc3f873e6.csv
../data/output/0/05ca2180d1a20feab0a4a26fc3f873e6.mid
../data/output/0/079179ac79256ddd48244b046e7b4601.csv
../data/output/0/079179ac79256ddd48244b046e7b4601.mid
../data/output/0/0c53205c5b8ffc97d93289c8e3e40ca4.mid
../data/output/0/01b03255f15

...

../data/output/3/3a6a7428114af49cb76f962db188817f.csv
../data/output/3/3a6a7428114af49cb76f962db188817f.mid
../data/output/3/346242777c24097653f0d65b4c91226d.csv
../data/output/3/346242777c24097653f0d65b4c91226d.mid
../data/output/3/395e429617c2e494907401b61cf58caa.csv
../data/output/3/395e429617c2e494907401b61cf58caa.mid
../data/output/3/30a6d86d1f41695b16f16cf6e4e60249.csv
../data/output/3/30a6d86d1f41695b16f16cf6e4e60249.mid
../data/output/3/3463759c66ca27224bc8b873dc4581c4.csv
../data/output/3/3463759c66ca27224bc8b873dc4581c4.mid
../data/output/3/3eae2e081c9e8f17a5dee55a445e3d61.csv
../data/output/3/3eae2e081c9e8f17a5dee55a445e3d61.mid
../data/output/3/364ca3d40d5ca4b42a618844ca024bd7.csv
../data/output/3/3657e88faa22b11843f7afb630dc3a74.mid
../data/output/3/3af92d01a49db116a3332525a22326f7.csv
../data/output/3/3af92d01a49db116a3332525a22326f7.mid
../data/output/3/30a85a5ca6d1ed14f0830a53e249ca42.csv
../data/output/3/30a85a5ca6d1ed14f0830a53e249ca42.mid
../data/output/3/3123c2d1dcb

../data/output/3/3968b9fdd6b5a4a67dd1107429b28cd2.csv
../data/output/3/3ab20c642d61402915390591016a2958.csv
../data/output/3/3ab20c642d61402915390591016a2958.mid
../data/output/3/3ddedaa2d2428bdd7895545aa1f112ac.csv
../data/output/3/3ddedaa2d2428bdd7895545aa1f112ac.mid
../data/output/3/352c908c23c4c081da7c628dadfe2f72.csv
../data/output/3/352c908c23c4c081da7c628dadfe2f72.mid
../data/output/3/3ab262b56571f44969189891da501840.csv
../data/output/3/3ab262b56571f44969189891da501840.mid
../data/output/3/319dea56ea48cd7073bcdd5fdff95c4a.csv
../data/output/3/319dea56ea48cd7073bcdd5fdff95c4a.mid
../data/output/3/3c7524ee1d1b941d96f7f6abab067445.csv../data/output/3/350df56ca872f69a670d2859d041465d.csv

../data/output/3/350df56ca872f69a670d2859d041465d.mid../data/output/3/3c7524ee1d1b941d96f7f6abab067445.mid

../data/output/3/3cd77cb35bf7d146e154085051ba1b33.mid
../data/output/3/330d6eac20034828aa4adfb6431e0428.csv
../data/output/3/330d6eac20034828aa4adfb6431e0428.mid
../data/output/3/33493651846

../data/output/3/353ea8113fdc0526a07a61798df93e9e.mid
../data/output/3/3e2b4533e05903431c08613c5041059a.csv
../data/output/3/3c97929c7c73a1fe667424a278df2bbf.csv
../data/output/3/3c97929c7c73a1fe667424a278df2bbf.mid
../data/output/3/3fb1d3b187b1f477ffeacbfb0719a444.csv
../data/output/3/3fb1d3b187b1f477ffeacbfb0719a444.mid
../data/output/3/3762c2a305930c3ba1e95248568e1647.mid
../data/output/3/3f431fb49d8d15a3071b2a7e5443c7dc.csv
../data/output/3/3f431fb49d8d15a3071b2a7e5443c7dc.mid
../data/output/3/3ad017c722ab3591cf0edbb5d47b403d.mid
../data/output/3/3ac1408058023193002a13ab92b42bb3.csv
../data/output/3/390c984f4cd4cae0cca3c31fff304169.csv
../data/output/3/390c984f4cd4cae0cca3c31fff304169.mid
../data/output/3/3f4619944e7c824796255b4122c079fc.csv
../data/output/3/3f4619944e7c824796255b4122c079fc.mid
../data/output/3/388468377ee7b72919a7c3ca78c0eb3b.csv
../data/output/3/388468377ee7b72919a7c3ca78c0eb3b.mid
../data/output/3/3eb550863d8bc8a0a5ac360f97aeea72.csv
../data/output/3/3eb550863d8

../data/output/3/3d768e8e5e4f481e1a4413e05dc58eaf.csv
../data/output/3/3d768e8e5e4f481e1a4413e05dc58eaf.mid
../data/output/3/3dbb88e51cdaccc8d15115be2eba88bf.mid
../data/output/3/3c95992690ab58a8cb44c733bdd607c5.csv
../data/output/3/3c95992690ab58a8cb44c733bdd607c5.mid
../data/output/3/39f5f9aa940a221eec07414f48cc108f.csv
../data/output/3/39f5f9aa940a221eec07414f48cc108f.mid
../data/output/3/3673b26f4d18e93d9b09119e06603a42.csv
../data/output/3/3673b26f4d18e93d9b09119e06603a42.mid
../data/output/3/30bc0290958fffbc93f636f8fbab19a3.csv
../data/output/3/307b3abb608a9ff0fcec8297038189ca.mid
../data/output/3/39bb558a2839a527099b4dbb3ae062a4.csv
../data/output/3/39bb558a2839a527099b4dbb3ae062a4.mid
../data/output/3/307b73389589b9f633f13722e6fc3f4e.csv
../data/output/3/307b73389589b9f633f13722e6fc3f4e.mid
../data/output/3/3e6f3a52d596479441fd608232096f03.mid
../data/output/3/307bb3e64715fb017f6fd2d89b8e62ae.csv
../data/output/3/307bb3e64715fb017f6fd2d89b8e62ae.mid
../data/output/3/39f6bf81c67

../data/output/3/3cc75cf63919a86397144deb8e105262.mid
../data/output/3/369c2d4d09faca23b4e848fa7ca70f8c.csv
../data/output/3/369c2d4d09faca23b4e848fa7ca70f8c.mid
../data/output/3/3e5e4a6482a94d11ed3c972d8f396506.csv
../data/output/3/3e5e4a6482a94d11ed3c972d8f396506.mid
../data/output/3/3cc88322b9783d61ce17fa336ae033c3.csv
../data/output/3/3cc88322b9783d61ce17fa336ae033c3.mid
../data/output/3/3536fc51175c9e85dd6dd3e2cab604f3.csv
../data/output/3/3536fc51175c9e85dd6dd3e2cab604f3.mid
../data/output/3/369d50fe4a58ddca8a7f49500a61d539.csv
../data/output/3/369d50fe4a58ddca8a7f49500a61d539.mid
../data/output/3/369e203397cd1d6dc71db25de39aca93.csv
../data/output/3/369e203397cd1d6dc71db25de39aca93.mid
../data/output/3/35396e7313d12f0f13493665493f88fb.csv
../data/output/3/35396e7313d12f0f13493665493f88fb.mid
../data/output/3/3e5f368ea8a406ac212176640c9ba69a.csv
../data/output/3/3e5f368ea8a406ac212176640c9ba69a.mid
../data/output/3/3e5f8fbb12a0bc8c22f04288b6481e4a.csv
../data/output/3/3e5f8fbb12a

In [16]:
pool.terminate() 

In [21]:
from functools import partial
import multiprocessing

transpose = False
chord_processor = ChordProcessor('../pickles/chord_profile.pkl', '../pickles/key_map.pkl')
chordino = Chordino(roll_on=5)


# folders = list(range(0, 10)) + ['a', 'b', 'c', 'd', 'e', 'f']
folders = ['b', 'c', 'd', 'e', 'f']


iterable = []
for folder in folders:
    directory = f'../data/output/{folder}'
    
    for dirpath,_,filenames in os.walk(directory):
        for f in filenames:
            iterable.append(os.path.join(dirpath, f))

# print(len(iterable))
# print(iterable[1])

# extract_chords_and_melody(transpose, chord_processor, chordino, iterable[2])

pool = multiprocessing.Pool(8)

func = partial(extract_chords_and_melody, transpose, chord_processor, chordino)

pool.map(func, iterable)
pool.close()
pool.join()

../data/output/b/b835a1b137626aabbcd6cc320a86a919.mid../data/output/b/b001b4efb265c4ad98a408bb12ecf581.csv../data/output/b/bb2ed0c87844d55519457a1709921cc6.mid../data/output/b/bc0d90d188ef07cb378040a1ccdbf9ab.mid../data/output/b/b5a392caea52f5dfc843d4c8b0594b54.mid../data/output/b/b09178389d82aa33a9c839768f59cdce.mid../data/output/b/b611d880b30e4c90c60dd8d607774ed2.mid../data/output/c/c1e5b162efd081b47f17546ed2a2cfb9.mid







../data/output/b/b001b4efb265c4ad98a408bb12ecf581.mid
../data/output/b/b612bd9b32c0c7e5cb4b2e70d1d27123.mid
../data/output/b/b5a3bf5c2925cf16243602e004f13e5e.mid
../data/output/b/b836a06a1a3f6a4cf0a879008895db3f.mid
../data/output/b/b0919214d29730cfa8f0fc30149d87a0.mid
../data/output/b/bc0dbea4d9c6af2e4fbd2f3ca28f070c.mid
../data/output/b/b5a4db1052e4584472a2e9a225b9d3ac.mid
../data/output/b/bb3046bf075f16312c133455d6315f09.mid
../data/output/b/b3cff3eeec66fe9f448c8aee6de784f8.mid
../data/output/b/b002c0561e5337264cb1e25dce84e14a.csv
../data/output/b/b002c0561e5

../data/output/b/bfb829ba4dddca341aea524e0574712a.mid
../data/output/c/c2bc458a5c86de6bb6748a77125c6f3e.mid
../data/output/b/b5d21079dcdaf6115a1feb04632d4b3e.mid
../data/output/b/bd87dbadcf45da9b77949bd95702a742.mid
../data/output/b/b83d95b561ecd881e3b4b0d18320ec78.mid
../data/output/b/be26de361cc6abf810a04a1ee75356ad.mid
../data/output/b/b5d28fcd777cc09652667d215ffd469f.mid
../data/output/b/bfb86f1be82a1872a1f409f591d7d2a0.mid
../data/output/b/bd974bf5fa20200ae6f43d6e076930f7.mid
../data/output/c/c2bde103d6bc53e312c3dbd62b9e2b50.mid
../data/output/b/b7530b1495492fa9f88053411a8ac5b8.mid
../data/output/b/bd977dea021c1aa333afe4b55f3abead.mid
../data/output/b/b75317eadb004899ba077786e5b7fdf2.mid
../data/output/c/c2beba2051046c6f4f4f620ce215fd2a.mid
../data/output/b/b5d29b85528d6ecf636138545061fb80.mid
../data/output/b/bfbaa71a9646c983e5470c58df1e7119.mid
../data/output/b/b7547594f6c5e1b5b34f0bccf16fd407.mid
../data/output/b/b006d622d5ac66ec97716a2e740cc0b4.csv
../data/output/b/b01286cfa5d

../data/output/b/b0bc87fe63b4df1e60d7b26d59477231.mid
../data/output/b/be8980d2f3c27ceefc5d06e979513adf.mid
../data/output/b/b4e2f714eb29ab8061f7db07c2a4bc2e.mid
../data/output/b/bbef80a8a0a2882c34759b93e311471f.mid
../data/output/b/b5c05323f19a8ffbabfc89261f53125b.mid
../data/output/b/b1b33496f1e35f74c3567d9c4daf5d0b.mid
../data/output/b/b3873990c90cfd2a6fe3ae8040ecb0af.mid
../data/output/b/be8a010bd5df0410373d8ff8ebe0656c.mid
../data/output/b/bbf02b0de87bf08f55e04cddcbb382c6.mid
../data/output/b/b0bc9be00864d56e6e7b21477617494e.mid
../data/output/b/b4e30b7083499ce5f2e3c21c5616b029.mid
../data/output/b/b1b33ff0afaa50e9da76787521d0a12e.mid
../data/output/b/b5c0d9e059917daa44f4d4bc4e8416cc.mid
../data/output/b/b388871f5eca6f6470c8cd9974209d6e.mid
../data/output/b/b5454938e6d99fa8ff78c9741be67f27.mid
../data/output/b/bbf08f3439f3abb9c140bf572d92eae2.mid
../data/output/b/b0bd22bfcc3be417e88eb64f13b9942d.mid
../data/output/b/b1b3d0631e5c167dcaf2ba0073992107.mid
../data/output/b/b4e33373602

../data/output/b/b51547a405953109a0388254aacb27cb.mid
../data/output/c/c173fd0af75a8e9900b4570dee0093a4.mid
../data/output/b/bac6df81569e2a3c6bcec6c65ab3a866.mid
../data/output/b/bac70a94f1492cc1f2deda32f677471a.mid
../data/output/b/b51d764a5e4d252b7fd7befafd37235b.mid
../data/output/b/ba29d81b9a4ef014684cdacd65a9104e.mid
../data/output/b/b648dbacbce721662bea5cd72e3a2d76.mid
../data/output/b/bb5a44a0e62320d56218501a6ad4533d.mid
../data/output/c/c17409e7085684ec70fb6a211522dcd7.mid
../data/output/b/bc5c1adfe5b08232f1b931f13aec52e8.mid
../data/output/b/b64bcc922bf0e1df61e7a8e3fdd0f82a.mid
../data/output/b/b0cfcff0ba23e3887992126bb20892d4.mid
../data/output/b/bb5b3306a54e20dd5ad44b15d45b6b79.mid
../data/output/b/b0d01f81844e22e6a90897f8e86bb680.mid
../data/output/b/b52d08716baa33f47b61c2ab39b6f33a.mid
../data/output/b/bac8b28028c535084e554c3e2a9d53cb.mid
../data/output/b/b64c96ddc87576da30e01df6b3a9437e.mid
../data/output/c/c175323dbdff4b676588609081bf5606.mid
../data/output/b/b53ad6cbbfb

../data/output/b/b658045d4b64db89ac8d9859c166b62a.csv
../data/output/b/b658045d4b64db89ac8d9859c166b62a.mid
../data/output/b/b029744fdc7d1f0caa45d7bed08e5a40.mid
../data/output/b/bd1ba29cc64ebf5da7d00aa6b6ad2cbd.csv
../data/output/b/bd1ba29cc64ebf5da7d00aa6b6ad2cbd.mid
../data/output/b/b6586240e5db62c0ba241e09c0fb972b.csv
../data/output/b/b6586240e5db62c0ba241e09c0fb972b.mid
../data/output/b/b658b993b9625f908ee65f9ccd5e5196.csv
../data/output/b/b658b993b9625f908ee65f9ccd5e5196.mid
../data/output/b/bdac69913ff40d8309eba1de2ebe4568.mid
../data/output/b/bbd90c2f875c861ae58a9e26a41fe21f.mid
../data/output/b/bedf8717d73f050538948832158b9872.mid
../data/output/c/c124faf6a88a3ecec299d97b4d9c7fe7.mid
../data/output/b/bd1ce590e23a42e5341a8a6dd6968abd.csv
../data/output/b/bd1ce590e23a42e5341a8a6dd6968abd.mid
../data/output/b/b029f258273624a36950ca50c575fd89.mid
../data/output/b/b659579731d798fdf4f881a119eede31.csv
../data/output/b/b659579731d798fdf4f881a119eede31.mid
../data/output/b/bbda551139b

...

../data/output/f/f90faa4f18e02071693e8bb30647ad8c.mid
../data/output/f/fd160b595a6d0a06fff80027512da4be.mid
../data/output/f/f1456b6a7c3dceb899afe6b52dbd563f.mid
../data/output/f/f33b6e9cb1d05fc085890aaa18aa5f45.mid
../data/output/f/fd2055b4ad7bd4758bb40b8c3be3e14a.mid
../data/output/f/f5488df7fc0e3c3cefdf91d21c414075.mid
../data/output/f/f911797610cc0e21978008971f1f4640.mid
../data/output/f/ffbf3fa78bee4153540fe5621e2c144a.mid
../data/output/f/f91337a2bcd774e9fab017d5284510ab.mid
../data/output/f/f33c1342fac8be6af23ef86b0237496d.mid
../data/output/f/fbcc6ab0b0a409fa6a6e34355a9d4d66.mid
../data/output/f/fd27ebc4b115528c02c7f59604b4f8b5.mid
../data/output/f/f146c45f9ae9b9033ac05e4064be1cf6.mid
../data/output/f/f54b067c0c187dd440b83fc3db9fb4f7.mid
../data/output/f/fbccc02042941e1a59f486f5489fd456.mid
../data/output/f/f1487712ef8f6d59a6d09d633f4508ea.mid
../data/output/f/f14a12b374c9e870aeed580fc42683d9.mid
../data/output/f/f33caaa8e5d3461b1afb2fcdd3f49546.mid
../data/output/f/f913a8b483c

../data/output/f/fa4d6c3c283f15b3dd8c27ff23c2dfae.mid
../data/output/f/fdb11b5f4730cd459a9e4ff06fcdd2e0.mid
../data/output/f/fd826a9529422e98e32c2a3ec41a7e19.mid
../data/output/f/f682262599f543f67d516ff90cad39d9.mid
../data/output/f/f1e64e481b08193e075de0950bf3121e.mid
../data/output/f/f1e694f1fbb205b9cbf06ee72e5fc54e.mid
../data/output/f/f20fcfefcbc242e034ab1252b7d83eb7.mid
../data/output/f/f7b34c825605fa3400e5a11dcaa8d496.mid
../data/output/f/f1e79e90c66f9de6fdb0f69f60c536ac.mid
../data/output/f/fdb2548d1c18449ef4b76fa9ce0bedd6.mid
../data/output/f/f2107b8d496e67989daa39c81f77be10.mid
../data/output/f/f682aed2087e983a3f2a2cc727abaac7.mid
../data/output/f/fd8d4006236c71586bff6c1f0e83ab12.mid
../data/output/f/f1e881d85fca7e6f52c92f9643c35e07.mid
../data/output/f/f898492d3ef632ecb36a39b29b252a80.mid
../data/output/f/f7b39e453ba2f6589e94e841769d07b4.mid
../data/output/f/f210eb05212c0ddfc6f1f6d95c89bb2b.mid
../data/output/f/fd9e6458a30d1e89d6f8f52ddba51dfe.mid
../data/output/f/feb37035d46

../data/output/f/f37d377cbddf765b5aca8b0811ffedae.mid
../data/output/f/f7c864349363cb9443abd33f95daf92c.mid
../data/output/f/f056ee922b73a0f81b12784ef665c2d0.mid
../data/output/f/fd73033d5a65c92534d4acfcc5b9e9fe.mid
../data/output/f/fef0ce865059f9fe417eddf30175b6e6.mid
../data/output/f/fb2c91719d5429b810a110813f5f97f1.mid
../data/output/f/f7c872f012410e6989d9d98499d399fb.mid
../data/output/f/f056f69e7f9b33a75f25033e2c16fede.mid
../data/output/f/f7c99929f1971ac7fb60ee0544219e12.mid
../data/output/f/f9623f748e87df5e569c740350dbcbcc.mid
../data/output/f/fb2dd8a5cc928a1352de2653dd79c773.mid
../data/output/f/fd7341025f9aea3a43577d9df5345ec3.mid
../data/output/f/f37e7214e84097c2fb3d024df6350819.mid
../data/output/f/f7c9a6486f4eff3ea3bc9b5cce76b34a.mid
../data/output/f/fb31333a86067527e1d89d2fdb1b261e.mid
../data/output/f/f9637b09c0e864d92b75e18c96406aa8.mid
../data/output/f/f7cafd3f9870ba42ef3bfdfb72b06714.mid
../data/output/f/f0580bc68c1479137178b44c1190a086.mid
../data/output/f/fef10260daa

../data/output/f/f2d84ca47f92235a955d4b2649c4bba3.mid
../data/output/f/fb75feec4224fd8731e7480624519652.mid
../data/output/f/f732857430c7a5c52ba0f6b975a61372.mid
../data/output/f/f669db868684ad8bf225742670340d0b.mid
../data/output/f/fb7861c6f6894ecb647d0135f23f7561.mid
../data/output/f/fec1e566480331160d3b86e6b14ceb15.mid
../data/output/f/ffa804393a22412746cbf0ccef09001a.mid
../data/output/f/f1a313c248d6c71aa333708ed8488556.mid
../data/output/f/f73327915f64502265f91d1c02dcd342.mid
../data/output/f/f16ec4e6c37b3c53caaefd225f0ddd5c.mid
../data/output/f/f1a3f9fc03300027ee7f96d4dd9e1348.mid
../data/output/f/ffa8a978207da0fad365fbad60d88c5b.mid
../data/output/f/f73346838ce4d3398b9978684614fe38.mid
../data/output/f/f669f7296649e791d0c5d0ab9625c9f2.mid
../data/output/f/fb78b55058dd614c1a447bc38fb06763.mid
../data/output/f/fb7987c03d5e20a98fc9e031f8051467.mid
../data/output/f/f16eeaccc8d19f22b6ece606185ada5d.mid
../data/output/f/f1a5575dfe75d65ae66a6ad17a7667ca.mid
../data/output/f/fec2346492a

../data/output/f/fcd82bc3d9efb1866d0510c3b30c789a.mid
../data/output/f/fef8ee16281d1a0cdf086d49423755f9.mid
../data/output/f/fb44517baddd2a46496850c39111d992.mid
../data/output/f/fa17e5f3d938a0bb19304f8beef995e6.mid
../data/output/f/f59a573c968a9e0f23475c0138a604c9.mid
../data/output/f/f8e3f7377227abd7e851ecace2ccc0c8.mid
../data/output/f/f59a94e01f5276bd8620053a772302cc.mid
../data/output/f/fcda28f718c5af47dc16157a9e5bcc98.mid
../data/output/f/fa18673aa6e5b721f629c0a602a9d00a.mid
../data/output/f/fefa856fa3789c9f74bf2d1e967eb293.mid
../data/output/f/f8e412e83573ad04ce9cbd181d3905ef.mid
../data/output/f/f59adee21123284d4ce209f911ab3079.mid
../data/output/f/fefb81e438109d913cdb39a3244c24b2.mid
../data/output/f/f8e4e9f210c69ae89c3f261f270e6839.mid
../data/output/f/fa18836d01fad3969986864bde72601b.mid
../data/output/f/f59b0c6412b6e4e76c8f3751727f632f.mid
../data/output/f/fcdad34c4e464926a2461309f975cd15.mid
../data/output/f/fcdb14fc9a56cbe4ceaecce564bff838.mid
../data/output/f/f59b1b8491a

In [22]:
pool.terminate() 